<a href="https://colab.research.google.com/github/vintagedeek/mnist/blob/master/kaggle_mnist_fully_connected_no_hidden_tanh.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import pandas as pd
import numpy as np

from collections import OrderedDict, namedtuple
from itertools import product
import time
from IPython.display import display, clear_output

import torch 
import torch.nn as nn 
import torch.optim as optim
import torch.nn.functional as F

In [2]:
train_url = "https://raw.githubusercontent.com/wehrley/Kaggle-Digit-Recognizer/master/train.csv"
df_train = pd.read_csv(train_url)
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 42000 entries, 0 to 41999
Columns: 785 entries, label to pixel783
dtypes: int64(785)
memory usage: 251.5 MB


In [3]:
test_url = 'https://raw.githubusercontent.com/wehrley/Kaggle-Digit-Recognizer/master/test.csv'
df_test = pd.read_csv(test_url)
df_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 28000 entries, 0 to 27999
Columns: 784 entries, pixel0 to pixel783
dtypes: int64(784)
memory usage: 167.5 MB


In [4]:
train_set = df_train[0:29400]
train = torch.tensor(np.array(train_set.iloc[:, 1:]), dtype=torch.torch.float32)
train_labels = torch.tensor(np.array(train_set.iloc[:, 0]), dtype=torch.int64)
val_set = df_train[29400:]
val = torch.tensor(np.array(val_set.iloc[:, 1:]), dtype=torch.float32)
val_labels = torch.tensor(np.array(val_set.iloc[:, 0]), dtype=torch.int64)

In [5]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'
device

'cuda'

In [6]:
train.shape

torch.Size([29400, 784])

In [7]:
29400/1000

29.4

In [8]:
network1 = nn.Sequential(
    nn.Linear(in_features=28*28, out_features=10),
    nn.Tanh())

networks = {
    'one_layer': network1, 
}

params = OrderedDict(
    lr = [1.0, 0.1, 0.01, 0.001, 0.0001, 0.00001],
    batch_size = [20, 30, 40, 50, 70, 100, 1000],
    device = ['cuda'],
    weight_decay = [0.01, 0.1, 1.0, 10.0],
    network = list(networks.keys())
)

class RunBuilder():
    @staticmethod
    def get_runs(params):

        Run = namedtuple('Run', params.keys())

        runs = []
        for v in product(*params.values()):
            runs.append(Run(*v))

        return runs

class RunManager():
    def __init__(self):
        self.epoch_count = 0
        self.epoch_loss = 0
        self.epoch_num_correct = 0
        self.epoch_start_time = None
        
        self.run_params = None
        self.run_count = 0
        self.run_data = []
        self.run_start_time = None
        
        self.network = None

       
    def begin_run(self, run, network):
        self.run_start_time = time.time()
        
        self.run_params = run
        self.run_count += 1
        
        self.network = network
        
    def end_run(self):
        self.epoch_count = 0
    
    def begin_epoch(self):
        self.epoch_start_time = time.time()
        self.epoch_count += 1
        self.epoch_loss = 0
        self.epoch_num_correct = 0
    
    def end_epoch(self):
        epoch_duration = time.time() - self.epoch_start_time
        run_duration = time.time() - self.run_start_time
        
        loss = self.epoch_loss / len(train)
        accuracy = self.epoch_num_correct / len(train)

            
        results = OrderedDict()
        results["run"] = self.run_count
        results['epoch'] = self.epoch_count
        results['loss'] = loss
        results['accuracy'] = accuracy
        results['epoch duration'] = epoch_duration
        results['run duration'] = run_duration
        for k, v in self.run_params._asdict().items(): results[k] = v
        self.run_data.append(results)
        df = pd.DataFrame.from_dict(self.run_data, orient='columns')
        clear_output(wait=True)
        display(df)
    
    def track_loss(self, loss):
        self.epoch_loss += loss.item() * 10
    
    def track_num_correct(self, preds, labels):
        self.epoch_num_correct += self._get_num_correct(preds, labels)
        
    @torch.no_grad()
    def _get_num_correct(self, preds, labels):
        return preds.argmax(dim=1).eq(labels).sum().item()
    
    def save(self, fileName): # save in json and csv
        
        pd.DataFrame.from_dict(self.run_data, orient='columns').to_csv(f'{fileName}.csv')
        
        with open(f'{fileName}.json', 'w', encoding='utf-8') as f:
            json.dump(self.run_data, f, ensure_ascii=False, indent=4)

m = RunManager()
for run in RunBuilder.get_runs(params):
    network = networks[run.network].to(device)
    mini_batches = [train[k:k + run.batch_size] for k in range(0, train_labels.shape[0], run.batch_size)]
    mini_labels = [train_labels[k:k + run.batch_size] for k in range(0, train_labels.shape[0], run.batch_size)]
    optimizer = optim.Adam(network.parameters(), lr=run.lr, weight_decay=run.weight_decay)

    m.begin_run(run, network)
    for epoch in range(40):
        m.begin_epoch()
        for b in range(0, len(mini_batches)):
            images = mini_batches[b].to(device)
            labels = mini_labels[b].to(device)
            preds = network(images) # pass batch
            loss = F.cross_entropy(preds, labels) # calculate loss
            optimizer.zero_grad() # zero gradients
            loss.backward() # calculate gradients
            optimizer.step() # update weights

            m.track_loss(loss)
            m.track_num_correct(preds, labels)
        m.end_epoch()

pd.DataFrame.from_dict(m.run_data).sort_values('accuracy', ascending=False)

run  epoch      loss  ...  device  weight_decay    network
0       1      1  1.363711  ...    cuda          0.01  one_layer
1       1      2  1.392384  ...    cuda          0.01  one_layer
2       1      3  1.382571  ...    cuda          0.01  one_layer
3       1      4  1.379863  ...    cuda          0.01  one_layer
4       1      5  1.390641  ...    cuda          0.01  one_layer
...   ...    ...       ...  ...     ...           ...        ...
6715  168   6716  0.009798  ...    cuda         10.00  one_layer
6716  168   6717  0.009801  ...    cuda         10.00  one_layer
6717  168   6718  0.009803  ...    cuda         10.00  one_layer
6718  168   6719  0.009805  ...    cuda         10.00  one_layer
6719  168   6720  0.009808  ...    cuda         10.00  one_layer

[6720 rows x 11 columns]

run  epoch      loss  ...  device  weight_decay    network
6641  167   6642  0.009512  ...    cuda          1.00  one_layer
6639  166   6640  0.009513  ...    cuda          0.10  one_layer
6640  167   6641  0.009520  ...    cuda          1.00  one_layer
6634  166   6635  0.009521  ...    cuda          0.10  one_layer
6638  166   6639  0.009515  ...    cuda          0.10  one_layer
...   ...    ...       ...  ...     ...           ...        ...
3135   79   3136  0.240926  ...    cuda          1.00  one_layer
644    17    645  0.397783  ...    cuda          0.01  one_layer
3141   79   3142  0.246275  ...    cuda          1.00  one_layer
329     9    330  0.691608  ...    cuda          0.01  one_layer
2818   71   2819  0.479555  ...    cuda          1.00  one_layer

[6720 rows x 11 columns]

In [9]:
pd.DataFrame.from_dict(m.run_data).sort_values('accuracy', ascending=False)[0:3]

run  epoch      loss  ...  device  weight_decay    network
6641  167   6642  0.009512  ...    cuda           1.0  one_layer
6639  166   6640  0.009513  ...    cuda           0.1  one_layer
6640  167   6641  0.009520  ...    cuda           1.0  one_layer

[3 rows x 11 columns]

In [11]:
pd.DataFrame.from_dict(m.run_data).sort_values('accuracy', ascending=False)[0:15]

run  epoch      loss  ...  device  weight_decay             network
236    6    237  1.208360  ...    cuda           1.0  one_hidden_layer30
221    6    222  1.209756  ...    cuda           1.0  one_hidden_layer30
206    6    207  1.208019  ...    cuda           1.0  one_hidden_layer30
772   20    773  0.600122  ...    cuda           0.1  one_hidden_layer30
222    6    223  1.207221  ...    cuda           1.0  one_hidden_layer30
223    6    224  1.210022  ...    cuda           1.0  one_hidden_layer30
226    6    227  1.210210  ...    cuda           1.0  one_hidden_layer30
230    6    231  1.209373  ...    cuda           1.0  one_hidden_layer30
218    6    219  1.210089  ...    cuda           1.0  one_hidden_layer30
213    6    214  1.206907  ...    cuda           1.0  one_hidden_layer30
233    6    234  1.208429  ...    cuda           1.0  one_hidden_layer30
210    6    211  1.210925  ...    cuda           1.0  one_hidden_layer30
239    6    240  1.212457  ...    cuda           1.0  one_hidden_layer30
770   20    771  0.605068  ...    cuda           0.1  one_hidden_layer30
204    6    205  1.212568  ...    cuda           1.0  one_hidden_layer30

[15 rows x 11 columns]

run  epoch      loss  ...  device  weight_decay              network
0    1      1  1.335997  ...    cuda          0.01  one_hidden_layer100

[1 rows x 11 columns]

run  epoch      loss  ...  device  weight_decay              network
0    1      1  1.335997  ...    cuda          0.01  one_hidden_layer100
1    1      2  1.324653  ...    cuda          0.01  one_hidden_layer100

[2 rows x 11 columns]

run  epoch      loss  ...  device  weight_decay              network
0    1      1  1.335997  ...    cuda          0.01  one_hidden_layer100
1    1      2  1.324653  ...    cuda          0.01  one_hidden_layer100
2    1      3  1.327232  ...    cuda          0.01  one_hidden_layer100

[3 rows x 11 columns]

run  epoch      loss  ...  device  weight_decay              network
0    1      1  1.335997  ...    cuda          0.01  one_hidden_layer100
1    1      2  1.324653  ...    cuda          0.01  one_hidden_layer100
2    1      3  1.327232  ...    cuda          0.01  one_hidden_layer100
3    1      4  1.325268  ...    cuda          0.01  one_hidden_layer100

[4 rows x 11 columns]

run  epoch      loss  ...  device  weight_decay              network
0    1      1  1.335997  ...    cuda          0.01  one_hidden_layer100
1    1      2  1.324653  ...    cuda          0.01  one_hidden_layer100
2    1      3  1.327232  ...    cuda          0.01  one_hidden_layer100
3    1      4  1.325268  ...    cuda          0.01  one_hidden_layer100
4    1      5  1.325853  ...    cuda          0.01  one_hidden_layer100

[5 rows x 11 columns]

...

run  epoch      loss  ...  device  weight_decay              network
0      1      1  1.335997  ...    cuda          0.01  one_hidden_layer100
1      1      2  1.324653  ...    cuda          0.01  one_hidden_layer100
2      1      3  1.327232  ...    cuda          0.01  one_hidden_layer100
3      1      4  1.325268  ...    cuda          0.01  one_hidden_layer100
4      1      5  1.325853  ...    cuda          0.01  one_hidden_layer100
..   ...    ...       ...  ...     ...           ...                  ...
832   21    833  0.644029  ...    cuda          1.00  one_hidden_layer100
833   21    834  0.642586  ...    cuda          1.00  one_hidden_layer100
834   21    835  0.643212  ...    cuda          1.00  one_hidden_layer100
835   21    836  0.645195  ...    cuda          1.00  one_hidden_layer100
836   21    837  0.644358  ...    cuda          1.00  one_hidden_layer100

[837 rows x 11 columns]

run  epoch      loss  ...  device  weight_decay              network
0      1      1  1.335997  ...    cuda          0.01  one_hidden_layer100
1      1      2  1.324653  ...    cuda          0.01  one_hidden_layer100
2      1      3  1.327232  ...    cuda          0.01  one_hidden_layer100
3      1      4  1.325268  ...    cuda          0.01  one_hidden_layer100
4      1      5  1.325853  ...    cuda          0.01  one_hidden_layer100
..   ...    ...       ...  ...     ...           ...                  ...
833   21    834  0.642586  ...    cuda          1.00  one_hidden_layer100
834   21    835  0.643212  ...    cuda          1.00  one_hidden_layer100
835   21    836  0.645195  ...    cuda          1.00  one_hidden_layer100
836   21    837  0.644358  ...    cuda          1.00  one_hidden_layer100
837   21    838  0.647199  ...    cuda          1.00  one_hidden_layer100

[838 rows x 11 columns]

run  epoch      loss  ...  device  weight_decay              network
0      1      1  1.335997  ...    cuda          0.01  one_hidden_layer100
1      1      2  1.324653  ...    cuda          0.01  one_hidden_layer100
2      1      3  1.327232  ...    cuda          0.01  one_hidden_layer100
3      1      4  1.325268  ...    cuda          0.01  one_hidden_layer100
4      1      5  1.325853  ...    cuda          0.01  one_hidden_layer100
..   ...    ...       ...  ...     ...           ...                  ...
834   21    835  0.643212  ...    cuda          1.00  one_hidden_layer100
835   21    836  0.645195  ...    cuda          1.00  one_hidden_layer100
836   21    837  0.644358  ...    cuda          1.00  one_hidden_layer100
837   21    838  0.647199  ...    cuda          1.00  one_hidden_layer100
838   21    839  0.644407  ...    cuda          1.00  one_hidden_layer100

[839 rows x 11 columns]

run  epoch      loss  ...  device  weight_decay              network
0      1      1  1.335997  ...    cuda          0.01  one_hidden_layer100
1      1      2  1.324653  ...    cuda          0.01  one_hidden_layer100
2      1      3  1.327232  ...    cuda          0.01  one_hidden_layer100
3      1      4  1.325268  ...    cuda          0.01  one_hidden_layer100
4      1      5  1.325853  ...    cuda          0.01  one_hidden_layer100
..   ...    ...       ...  ...     ...           ...                  ...
835   21    836  0.645195  ...    cuda          1.00  one_hidden_layer100
836   21    837  0.644358  ...    cuda          1.00  one_hidden_layer100
837   21    838  0.647199  ...    cuda          1.00  one_hidden_layer100
838   21    839  0.644407  ...    cuda          1.00  one_hidden_layer100
839   21    840  0.644977  ...    cuda          1.00  one_hidden_layer100

[840 rows x 11 columns]

KeyboardInterrupt: ignored